# correctAtomicMismatch

Not all the proteins' atoms are being read correctly from the pdb file into the xyz file, for processing.

This error occurs in generateXYZFileTestCa.py

In this notebook we generate a small generateXYZFileTestCa.py testset, then iterate until its fixed. We also have code for checking it's fixed.

In [18]:
import quippy
import shutil

import ase
import json
from ase.atoms import Atoms as AseAtoms
import warnings
import os
import glob
import subprocess


In [45]:

path_to_xyz="/home/wpg/PhD/protein-networks-scaffolding/notebooks/BindingSVMWithDeepDrugDataset/intermediates/samples_filtered.xyz"
atom_reader = quippy.AtomsReader(path_to_xyz, format="xyz")
# Crude, but quick enough for now
protein = None
for temp_protein in atom_reader:
    ref, tag = temp_protein.params["tag"].split("_")
    if tag == "heme":
        shutil.copyfile("/home/wpg/PhD/protein-networks-scaffolding/notebooks/BindingSVMWithDeepDrugDataset/inputs/protein-heme/{}.pdb".format(ref),
                        "hemes/{}.pdb".format(ref))
    elif tag == "nucleo":
        shutil.copyfile("/home/wpg/PhD/protein-networks-scaffolding/notebooks/BindingSVMWithDeepDrugDataset/inputs/protein-nucleotide/{}.pdb".format(ref),
                        "nucleos/{}.pdb".format(ref))


In [46]:
!ls nucleos

1esqC.pdb  1y56A.pdb  2pc9B.pdb  3lgxC.pdb  4g5yA.pdb  4x2dA.pdb  5j1sA.pdb
1gn8A.pdb  1yfrA.pdb  2r9vA.pdb  3meyB.pdb  4gxqB.pdb  4xhoA.pdb  5l9nA.pdb
1ii0B.pdb  1ytmA.pdb  2rsfA.pdb  3qx9C.pdb  4h2uB.pdb  4xruB.pdb  5m7nA.pdb
1ji0A.pdb  1zaoA.pdb  2xszC.pdb  3sl2A.pdb  4itmA.pdb  4zqxA.pdb  5mb9B.pdb
1ko5A.pdb  1zfnA.pdb  2xtiB.pdb  3umoA.pdb  4kr7A.pdb  5burA.pdb  5mcpH.pdb
1mjhB.pdb  2biyA.pdb  2yaaA.pdb  3w1gA.pdb  4mb2B.pdb  5d6jA.pdb  5tgcD.pdb
1nyrA.pdb  2cjaB.pdb  3amtA.pdb  3wbzE.pdb  4mwhA.pdb  5d9hB.pdb  5uj7A.pdb
1tc0B.pdb  2ixfB.pdb  3epsA.pdb  4dxlA.pdb  4ndoB.pdb  5dn6F.pdb  5uj7C.pdb
1uf9C.pdb  2j3mB.pdb  3hgmA.pdb  4f6tA.pdb  4nh0B.pdb  5f1cB.pdb  5v2lA.pdb
1xexA.pdb  2jjxB.pdb  3ie7A.pdb  4fg9B.pdb  4v02A.pdb  5i0nA.pdb  5vqaA.pdb
1xmiD.pdb  2kmxA.pdb  3innD.pdb  4fvqA.pdb  4wc0B.pdb  5i9eA.pdb


In [47]:
!ls hemes

1ashA.pdb  1f1cA.pdb  1ix3A.pdb  1x9fB.pdb  2r1hB.pdb  3nn2B.pdb  4n4jA.pdb
1bvbA.pdb  1fj0A.pdb  1j77A.pdb  1xq5A.pdb  2r79A.pdb  3pt7B.pdb  4n4oA.pdb
1ccrA.pdb  1fs7A.pdb  1jebA.pdb  1yeaA.pdb  2v7iA.pdb  3qjtA.pdb  4nk2A.pdb
1co6A.pdb  1gcvA.pdb  1jjuA.pdb  1yhuC.pdb  2vzwB.pdb  3rwlA.pdb  4oqrA.pdb
1cpqA.pdb  1gdiA.pdb  1ls9A.pdb  2bz9A.pdb  2wh8B.pdb  3tf8B.pdb  4uiiA.pdb
1cxaA.pdb  1gksA.pdb  1m7sA.pdb  2c2cA.pdb  2zooA.pdb  3vliA.pdb  4uiqA.pdb
1cxyA.pdb  1hbgA.pdb  1ntfA.pdb  2czsA.pdb  3a4hA.pdb  3zhwA.pdb  4xe3A.pdb
1dvhA.pdb  1hbhA.pdb  1oagA.pdb  2d09A.pdb  3b42A.pdb  4b8nB.pdb  5cx7E.pdb
1dvvA.pdb  1hbhB.pdb  1os6A.pdb  2d2mA.pdb  3bxuB.pdb  4egnB.pdb  5de0C.pdb
1ebtA.pdb  1hlmA.pdb  1prhA.pdb  2d2mB.pdb  3czhA.pdb  4ejgE.pdb  5fygA.pdb
1ecaA.pdb  1hroA.pdb  1s56B.pdb  2flqB.pdb  3gw9A.pdb  4gu7A.pdb  5lthA.pdb
1etpA.pdb  1it2A.pdb  1schB.pdb  2j0pA.pdb  3hyuA.pdb  4i91A.pdb
1ew6A.pdb  1ithA.pdb  1x9fA.pdb  2olpA.pdb  3mk7A.pdb  4jouA.pdb


In [26]:
# Because of the daft labelling, I need to strip all the element symbols and relabel them.
def relabelElementNames(filePath, only_keep_alphas=False):
    with open(proteinLabel) as flines:
        data = [line.strip() for line in flines]
    new_data = []
    for line in data:
        if not line.startswith("ATOM"):
            # Do nothing
            new_data.append(line)
            continue
        atom_name = line[12:16]
        if only_keep_alphas and atom_name.strip() == "CA":
            # convert the CA to a C and push to the new file
            new_line = line[:12] + line[12:16].replace("CA", "C ") + line[16:]
            new_data.append(new_line)
        elif not only_keep_alphas:
            # replace C* with C, S* with S, N* with N, O* with O
            if not line[13].strip():
                raise IndexError("the spacing is off!")
            if line[13] not in ["C", "S", "N", "O", "H"]:
                print "Warning", line[12:16]
            new_line = line[:14] + "  " + line[16:]
            new_data.append(new_line)
    newLabel = proteinLabel[:-4] + "_converted" + proteinLabel[-4:]
    with open(newLabel, "w") as flines:
        flines.write("\n".join(new_data))
    return newLabel




In [66]:
hemeInputDir = "hemes"
hemeProteins = os.listdir(hemeInputDir)
print(len(hemeProteins), "proteins in heme directory")

nucleoInputDir = "nucleos"
nucleoProteins = os.listdir(nucleoInputDir)
print(nucleoInputDir)
print(len(nucleoProteins), "proteins in nucleotide directory")

proteinHolder = []
labels = []
for hemeLabel in hemeProteins:
    proteinLabel = hemeInputDir + "/" + hemeLabel
    newLabel = relabelElementNames(proteinLabel, False)
    try:
        temp = quippy.Atoms(ase.io.read(newLabel, format='proteindatabank')) # done like this to catch warning
        proteinHolder.append(temp)
        labels.append([hemeLabel, "heme"])
    except Warning:
        print("!!")
        continue
for nucleoLabel in nucleoProteins:
    proteinLabel = nucleoInputDir + "/" + nucleoLabel
    newLabel = relabelElementNames(proteinLabel, False)
    try:
        temp = quippy.Atoms(ase.io.read(newLabel, format='proteindatabank')) # done like this to catch warning
        proteinHolder.append(temp)
        labels.append([nucleoLabel, "nucleo"])
    except Warning:
        print("!!")
        continue

with open("test_labels.txt", "w") as flines:
    flines.write("\n".join(" ".join(x) for x in labels))

testFamily = quippy.AtomsList(proteinHolder)
print(len(testFamily), "proteins converted to xyz")
print(len(labels), "labels listed")
testFamily.write("test_proteinstructures.xyz")

xyzFileName= "test_proteinstructures.xyz"
with open(xyzFileName) as flines:
    data = [line.strip() for line in flines]
newdata = []
counter = 0 
for line in data:
    if line.startswith("cutoff"):
        print(labels[counter])
        label = labels[counter][0][:-4] + "_" + labels[counter][1]
        line += " tag=\"{}\" ".format(label)
        counter += 1
    newdata.append(line)
assert len(newdata) == len(data)
assert len(labels) == counter
with open("test_proteinstructures_tagged.xyz", "w") as flines:
    flines.write("\n".join(newdata))

(89, 'proteins in heme directory')
nucleos
(76, 'proteins in nucleotide directory')


KeyboardInterrupt: 

Now run the code giving the difference between the xyz file and the original dataset 

In [64]:
def checkMismatch(path_to_xyz, verbose=False):
#     path_to_xyz="test_proteinstructures_tagged.xyz"
    proteins = quippy.AtomsReader(path_to_xyz, format="xyz")
    for protein in proteins:
    # Crude, but quick enough for now
        xyz_positions = protein.arrays["positions"]
        tag =protein.params["tag"]
        pdb_ref = tag[:4]
        chain_ref = tag[4]
        print(pdb_ref,chain_ref)
        if not os.path.exists("{}.pdb".format(pdb_ref)):
            subprocess.call(["wget","http://www.rcsb.org/pdb/files/{}.pdb".format(pdb_ref), "-q"])
        with open("{}.pdb".format(pdb_ref)) as flines:
            pdb_data = flines.readlines()
        raw_data = []
        missing_lines = []
        for line in pdb_data:
            if line.startswith("ATOM") and line[21] == chain_ref:
                raw_data.append(line)
                positions = [float(line[30:38]), float(line[38:46]), float(line[46:54])]
                if positions not in xyz_positions:
                    missing_lines.append(line)
        print(len(raw_data), len(xyz_positions))
        print("\n".join(missing_lines))

#     xyz_positions = protein.arrays["positions"]
    
#     with open("4eie.pdb") as flines:
#         chain_ref = "A"
#         pdb_data = [line.strip() for line in flines]
#         raw_data = []
#         for line in pdb_data:
#             if line.startswith("ATOM") and line[21] == chain_ref:
#                 positions = [float(line[30:38]), float(line[38:46]), float(line[46:54])]
#                 if positions not in xyz_positions:
#                     print(line)


# import glob
# import subprocess
# import os

# DIR_NAME = "outputs_r5"

# for datfile in glob.glob(f"{DIR_NAME}/*.dat"):
#     print(datfile)
#     with open(datfile) as flines:
#         data = [line.strip().split(" ") for line in flines]
#     print(len(data))
#     datfilename = datfile.split("/")[1]
#     pdb_ref = datfilename[:4]
#     chain_ref = datfilename[4]
#     if not os.path.exists(f"{pdb_ref}.pdb"):
#         subprocess.call(["wget","http://www.rcsb.org/pdb/files/{}.pdb".format(pdb_ref), "-q"])
#     with open("{}.pdb".format(pdb_ref)) as flines:
#         pdb_data = flines.readlines()
#     raw_data = []
#     for line in pdb_data:
#         if line.startswith("ATOM") and line[21] == chain_ref:
#             raw_data.append(line)
#     print(len(raw_data))


In [36]:
# Because of the daft labelling, I need to strip all the element symbols and relabel them.
def relabelElementNamesCorrected(filePath, only_keep_alphas=False):
    with open(proteinLabel) as flines:
        data = [line.strip() for line in flines]
    new_data = []
    for line in data:
        if not line.startswith("ATOM"):
            # Do nothing
            new_data.append(line)
            continue
        atom_name = line[12:16]
        print(atom_name)
        atom_element_symbol = line[76:78]
        print(atom_element_symbol)
#         if only_keep_alphas and atom_name.strip() == "CA":
#             # convert the CA to a C and push to the new file
#             new_line = line[:12] + line[12:16].replace("CA", "C ") + line[16:]
#             new_data.append(new_line)
#         elif not only_keep_alphas:
#             # replace C* with C, S* with S, N* with N, O* with O
#             if not line[13].strip():
#                 raise IndexError("the spacing is off!")
#             if line[13] not in ["C", "S", "N", "O", "H"]:
#                 print "Warning", line[12:16]
#             new_line = line[:14] + "  " + line[16:]
#             new_data.append(new_line)
#     newLabel = proteinLabel[:-4] + "_converted" + proteinLabel[-4:]
#     with open(newLabel, "w") as flines:
#         flines.write("\n".join(new_data))
#     return newLabel

In [37]:
hemeInputDir = "hemes"
hemeProteins = os.listdir(hemeInputDir)
print(len(hemeProteins), "proteins in heme directory")

nucleoInputDir = "nucleos"
nucleoProteins = os.listdir(nucleoInputDir)
print(len(nucleoProteins), "proteins in nucleotide directory")

proteinHolder = []
labels = []
for hemeLabel in hemeProteins:
    proteinLabel = hemeInputDir + "/" + hemeLabel
    newLabel = relabelElementNamesCorrected(proteinLabel, False)

(93, 'proteins in heme directory')
(99, 'proteins in nucleotide directory')
 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 CG 




 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 ND1

 CD2

 CE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 NE1

 CE2

 CE3

 CZ2

 CZ3

 CH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB


 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 SG 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 ND1

 CD2

 CE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N 

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  


 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 ND1

 CD2

 CE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 NE1

 CE2

 CE3

 CZ2

 CZ3

 CH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 SD 

 CE 

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 ND1

 CD2

 CE1

 NE2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA

...


 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 ND1

 CD2

 CE1

 NE2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C 


 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 SD 

 CE 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 CE 

 NZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 ND2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA


 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 SD 

 CE 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 OH 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG

 CB 

 CG 

 CD1

 CD2

 NE1

 CE2

 CE3

 CZ2

 CZ3

 CH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG 

 ND1

 CD2

 CE1

 NE2

 N  

 CA 

 C  

 O  

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 CD1

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 


 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 OE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 OE1

 NE2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 SD 

 CE 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD 

 NE 

 CZ 

 NH1

 NH2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 NE1

 CE2

 CE3

 CZ2

 CZ3

 CH2

 N  

 CA 

 C  

 O  

 CB 

 OG 

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 OD1

 OD2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 N  

 CA 

 C  

 O  

 CB 

 CG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 OG1

 CG2

 N  

 CA 

 C  

 O  

 CB 

 CG 

 CD1

 CD2

 CE1

 CE2

 CZ

### Turns out this dataset is even poorer than we thought. They've stripped out the element names, so we can't easily fix the labelling issue.

Instead, let's just use the list of proteins as a guide. Read in the list, take the pdb and chain.
Pull the data from the RCSB. Check that there's a HEM or an ATP in there. Remove the atom names, and replace them with the element name.


In [75]:
def generateXYZfile():
    
    hemeInputDir = "hemes"
    hemeProteins = os.listdir(hemeInputDir)
    print(len(hemeProteins), "proteins in heme directory")

    nucleoInputDir = "nucleos"
    nucleoProteins = os.listdir(nucleoInputDir)
    print(len(nucleoProteins), "proteins in nucleotide directory")

    proteinHolder = []
    labels = []
    
    if not os.path.exists("hemes_converted"):
        os.mkdir("hemes_converted")
    if not os.path.exists("nucleos_converted"):
        os.mkdir("nucleos_converted")

        
    for hemeLabel in hemeProteins:
        pdb_ref = hemeLabel[:4]
        chain_ref = hemeLabel[4]

        if not os.path.exists("{}.pdb".format(pdb_ref)):
            subprocess.call(["wget","http://www.rcsb.org/pdb/files/{}.pdb".format(pdb_ref), "-q"])
        with open("{}.pdb".format(pdb_ref)) as flines:
            pdb_data = [line.strip() for line in flines]
        
        raw_data = []
        ligand_found = False
        for line in pdb_data:
            if line.startswith("HETATM") and line[17:20].strip() == "HEM" and line[21] == chain_ref:
                ligand_found = True            
            if line.startswith("ATOM") and line[21] == chain_ref:
                raw_data.append(line)
        if not ligand_found:
            raise IOError

        newLabel = "hemes_converted/{}{}_heme.pdb".format(pdb_ref, chain_ref)
            
        with open(newLabel, "w") as flines:
            flines.write("\n".join(raw_data))
            
        temp = quippy.Atoms(ase.io.read(newLabel, format='proteindatabank')) # done like this to catch warning
        proteinHolder.append(temp)
        labels.append([pdb_ref+chain_ref, "heme"])

        
    for nucleoLabel in nucleoProteins:
        pdb_ref = nucleoLabel[:4]
        chain_ref = nucleoLabel[4]

        if not os.path.exists("{}.pdb".format(pdb_ref)):
            subprocess.call(["wget","http://www.rcsb.org/pdb/files/{}.pdb".format(pdb_ref), "-q"])
        with open("{}.pdb".format(pdb_ref)) as flines:
            pdb_data = [line.strip() for line in flines]
        
        raw_data = []
        ligand_found = False
        for line in pdb_data:
            if line.startswith("HETATM") and line[17:20].strip() == "ATP" and line[21] == chain_ref:
                ligand_found = True            
            if line.startswith("ATOM") and line[21] == chain_ref:
                raw_data.append(line)
        if not ligand_found:
            raise IOError

        newLabel = "nucleos_converted/{}{}_nucleo.pdb".format(pdb_ref, chain_ref)
            
        with open(newLabel, "w") as flines:
            flines.write("\n".join(raw_data))
            
        temp = quippy.Atoms(ase.io.read(newLabel, format='proteindatabank')) # done like this to catch warning
        proteinHolder.append(temp)
        labels.append([pdb_ref+chain_ref, "nucleo"])
            
    with open("test_labels.txt", "w") as flines:
        flines.write("\n".join(" ".join(x) for x in labels))

    testFamily = quippy.AtomsList(proteinHolder)
    print(len(testFamily), "proteins converted to xyz")
    print(len(labels), "labels listed")
    testFamily.write("test_proteinstructures.xyz")

    xyzFileName= "test_proteinstructures.xyz"
    with open(xyzFileName) as flines:
        data = [line.strip() for line in flines]
    newdata = []
    counter = 0 
    for line in data:
        if line.startswith("cutoff"):
            label = labels[counter][0] + "_" + labels[counter][1]
            line += " tag=\"{}\" ".format(label)
            counter += 1
        newdata.append(line)
    assert len(newdata) == len(data)
    assert len(labels) == counter
    with open("test_proteinstructures_tagged.xyz", "w") as flines:
        flines.write("\n".join(newdata))  
        proteinLabel = hemeInputDir + "/" + hemeLabel

In [74]:
generateXYZfile()

(89, 'proteins in heme directory')
(76, 'proteins in nucleotide directory')
(165, 'proteins converted to xyz')
(165, 'labels listed')
['1oagA', 'heme']
1oagA_heme
['1ew6A', 'heme']
1ew6A_heme
['4n4oA', 'heme']
4n4oA_heme
['4jouA', 'heme']
4jouA_heme
['1etpA', 'heme']
1etpA_heme
['4gu7A', 'heme']
4gu7A_heme
['4i91A', 'heme']
4i91A_heme
['3qjtA', 'heme']
3qjtA_heme
['2czsA', 'heme']
2czsA_heme
['1cxyA', 'heme']
1cxyA_heme
['1ebtA', 'heme']
1ebtA_heme
['1gdiA', 'heme']
1gdiA_heme
['5lthA', 'heme']
5lthA_heme
['1schB', 'heme']
1schB_heme
['1hbhB', 'heme']
1hbhB_heme
['2j0pA', 'heme']
2j0pA_heme
['1yhuC', 'heme']
1yhuC_heme
['1x9fB', 'heme']
1x9fB_heme
['5cx7E', 'heme']
5cx7E_heme
['2d2mA', 'heme']
2d2mA_heme
['1fj0A', 'heme']
1fj0A_heme
['1m7sA', 'heme']
1m7sA_heme
['1ashA', 'heme']
1ashA_heme
['3tf8B', 'heme']
3tf8B_heme
['3mk7A', 'heme']
3mk7A_heme
['3vliA', 'heme']
3vliA_heme
['1x9fA', 'heme']
1x9fA_heme
['1bvbA', 'heme']
1bvbA_heme
['1j77A', 'heme']
1j77A_heme
['1cxaA', 'heme']
1cxaA_h

In [77]:
checkMismatch(path_to_xyz="test_proteinstructures_tagged.xyz")

('1oag', 'A')
(1905, 1905)

('1ew6', 'A')
(1096, 1096)

('4n4o', 'A')
(4018, 4018)

('4jou', 'A')
(1259, 1259)

('1etp', 'A')
(1378, 1378)

('4gu7', 'A')
(2363, 2363)

('4i91', 'A')
(3757, 3757)

('3qjt', 'A')
(4409, 4409)

('2czs', 'A')
(564, 564)

('1cxy', 'A')
(639, 639)

('1ebt', 'A')
(1036, 1036)

('1gdi', 'A')
(1177, 1177)

('5lth', 'A')
(2756, 2756)

('1sch', 'B')
(2180, 2180)

('1hbh', 'B')
(1138, 1138)

('2j0p', 'A')
(2667, 2667)

('1yhu', 'C')
(1072, 1072)

('1x9f', 'B')
(1148, 1148)

('5cx7', 'E')
(1031, 1031)

('2d2m', 'A')
(1065, 1065)

('1fj0', 'A')
(847, 847)

('1m7s', 'A')
(3820, 3820)

('1ash', 'A')
(1239, 1239)

('3tf8', 'B')
(2826, 2826)

('3mk7', 'A')
(3683, 3683)

('3vli', 'A')
(5599, 5599)

('1x9f', 'A')
(1209, 1209)

('1bvb', 'A')
(1655, 1655)

('1j77', 'A')
(1588, 1588)

('1cxa', 'A')
(906, 906)

('4uiq', 'A')
(1252, 1252)

('3b42', 'A')
(964, 964)

('1f1c', 'A')
(1000, 1000)

('1gcv', 'A')
(1075, 1075)

('1hbg', 'A')
(1062, 1062)

('2v7i', 'A')
(2748, 2748)

('